<a href="https://colab.research.google.com/github/npgeorge/DS-Unit-2-Linear-Models/blob/master/Nicholas_George_Assignment_2_Regression_Classification.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Lambda School Data Science

*Unit 2, Sprint 1, Module 2*

---

# Regression 2

## Assignment

You'll continue to **predict how much it costs to rent an apartment in NYC,** using the dataset from renthop.com.

- [ ] Do train/test split. Use data from April & May 2016 to train. Use data from June 2016 to test.
- [ ] Engineer at least two new features. (See below for explanation & ideas.)
- [ ] Fit a linear regression model with at least two features.
- [ ] Get the model's coefficients and intercept.
- [ ] Get regression metrics RMSE, MAE, and $R^2$, for both the train and test data.
- [ ] What's the best test MAE you can get? Share your score and features used with your cohort on Slack!
- [ ] As always, commit your notebook to your fork of the GitHub repo.


#### [Feature Engineering](https://en.wikipedia.org/wiki/Feature_engineering)

> "Some machine learning projects succeed and some fail. What makes the difference? Easily the most important factor is the features used." — Pedro Domingos, ["A Few Useful Things to Know about Machine Learning"](https://homes.cs.washington.edu/~pedrod/papers/cacm12.pdf)

> "Coming up with features is difficult, time-consuming, requires expert knowledge. 'Applied machine learning' is basically feature engineering." — Andrew Ng, [Machine Learning and AI via Brain simulations](https://forum.stanford.edu/events/2011/2011slides/plenary/2011plenaryNg.pdf) 

> Feature engineering is the process of using domain knowledge of the data to create features that make machine learning algorithms work. 

#### Feature Ideas
- Does the apartment have a description?
- How long is the description?
- How many total perks does each apartment have?
- Are cats _or_ dogs allowed?
- Are cats _and_ dogs allowed?
- Total number of rooms (beds + baths)
- Ratio of beds to baths
- What's the neighborhood, based on address or latitude & longitude?

## Stretch Goals
- [ ] If you want more math, skim [_An Introduction to Statistical Learning_](http://faculty.marshall.usc.edu/gareth-james/ISL/ISLR%20Seventh%20Printing.pdf),  Chapter 3.1, Simple Linear Regression, & Chapter 3.2, Multiple Linear Regression
- [ ] If you want more introduction, watch [Brandon Foltz, Statistics 101: Simple Linear Regression](https://www.youtube.com/watch?v=ZkjP5RJLQF4)
(20 minutes, over 1 million views)
- [ ] Add your own stretch goal(s) !

In [0]:
%%capture
import sys

# If you're on Colab:
if 'google.colab' in sys.modules:
    DATA_PATH = 'https://raw.githubusercontent.com/LambdaSchool/DS-Unit-2-Applied-Modeling/master/data/'
    !pip install category_encoders==2.*

# If you're working locally:
else:
    DATA_PATH = '../data/'
    
# Ignore this Numpy warning when using Plotly Express:
# FutureWarning: Method .ptp is deprecated and will be removed in a future version. Use numpy.ptp instead.
import warnings
warnings.filterwarnings(action='ignore', category=FutureWarning, module='numpy')

In [0]:
import numpy as np
import pandas as pd

# Read New York City apartment rental listing data
df = pd.read_csv(DATA_PATH+'apartments/renthop-nyc.csv')
assert df.shape == (49352, 34)

# Remove the most extreme 1% prices,
# the most extreme .1% latitudes, &
# the most extreme .1% longitudes
df = df[(df['price'] >= np.percentile(df['price'], 0.5)) & 
        (df['price'] <= np.percentile(df['price'], 99.5)) & 
        (df['latitude'] >= np.percentile(df['latitude'], 0.05)) & 
        (df['latitude'] < np.percentile(df['latitude'], 99.95)) &
        (df['longitude'] >= np.percentile(df['longitude'], 0.05)) & 
        (df['longitude'] <= np.percentile(df['longitude'], 99.95))]

In [7]:
df.head()

bathrooms  bedrooms  ... wheelchair_access common_outdoor_space
0        1.5         3  ...                 0                    0
1        1.0         2  ...                 0                    0
2        1.0         1  ...                 0                    0
3        1.0         1  ...                 0                    0
4        1.0         4  ...                 0                    0

[5 rows x 34 columns]

In [8]:
df['created']

0        2016-06-24 07:54:24
1        2016-06-12 12:19:27
2        2016-04-17 03:26:41
3        2016-04-18 02:22:02
4        2016-04-28 01:32:41
                ...         
49347    2016-06-02 05:41:05
49348    2016-04-04 18:22:34
49349    2016-04-16 02:13:40
49350    2016-04-08 02:13:33
49351    2016-04-12 02:48:07
Name: created, Length: 48817, dtype: object

In [9]:
df.shape #original

(48817, 34)

In [0]:
df_copy = df

In [0]:
#confirmed training data is about twice as big as testing data, ok now lets add some features

#feature engineering

#lets try total number of rooms
df_copy['Rooms Total'] = df_copy['bedrooms'] + df_copy['bathrooms']

#how long is the description?
df_copy['Description Length'] = df_copy['description'].str.len() 

#how many perks?
df_copy['# of Perks'] = (df_copy['elevator']+
                    df_copy['cats_allowed']+
                    df_copy['hardwood_floors']+
                    df_copy['dogs_allowed']+
                    df_copy['doorman']+
                    df_copy['dishwasher']+	
                    df_copy['no_fee']+		
                    df_copy['laundry_in_building']+		
                    df_copy['fitness_center']+		
                    df_copy['pre-war']+		
                    df_copy['laundry_in_unit']+		
                    df_copy['roof_deck']+		
                    df_copy['outdoor_space']+		
                    df_copy['dining_room']+		
                    df_copy['high_speed_internet']+		
                    df_copy['balcony']+		
                    df_copy['swimming_pool']+		
                    df_copy['new_construction']+		
                    df_copy['terrace']+		
                    df_copy['exclusive']+		
                    df_copy['loft']+		
                    df_copy['garden_patio']+		
                    df_copy['wheelchair_access']+		
                    df_copy['common_outdoor_space'])

#cats or dogs
df_copy['Cats OR Dogs'] = (df_copy['cats_allowed'] | df_copy['dogs_allowed']) == 1

#cats and dogs
df_copy['Cats AND Dogs'] = (df_copy['cats_allowed'] & df_copy['dogs_allowed']) == 1

#beds to bath ratio
df_copy['Beds/Baths'] = df_copy['bedrooms'] / df_copy['bathrooms']

#neighborhood

#df_copy['Neighboorhood'] = 

In [0]:
#defining neighborhoods
#from geopy.geocoders import Nominatim
#df_lat_long = pd.DataFrame(df, columns = ['latitude', 'longitude']) 
#df_ll = pd.DataFrame(df_lat_long)
#df_ll = df_ll.to_string()
#location = geolocator.reverse(df_lat_long['latitude'][0], df_lat_long['longitude'][0])
#location
#lat_string = df_lat_long['latitude'].to_string()
#long_string = df_lat_long['longitude'].to_string()
#df_lat_long['lat&long'] = ()
#lat_string


In [12]:
#filtering dates for training model
df_copy['created'] = pd.to_datetime(df_copy['created'])

start_date = '04-01-2016 00:00:00'
end_date = '05-31-2016 23:59:59'

mask = (df_copy['created'] > start_date) & (df_copy['created'] <= end_date)

df_train = df_copy.loc[mask]

df_train.head()

bathrooms  bedrooms  ... Cats AND Dogs Beds/Baths
2        1.0         1  ...         False        1.0
3        1.0         1  ...         False        1.0
4        1.0         4  ...         False        4.0
5        2.0         4  ...         False        2.0
6        1.0         2  ...          True        2.0

[5 rows x 40 columns]

In [13]:
df_train.shape

(31844, 40)

In [14]:
#filtering dates for test model
df_copy['created'] = pd.to_datetime(df_copy['created'])

start_date = '06-01-2016 00:00:00'
end_date = '06-30-2016 23:59:59'

mask = (df_copy['created'] > start_date) & (df_copy['created'] <= end_date)

df_test = df_copy.loc[mask]

df_test.head()

bathrooms  bedrooms  ... Cats AND Dogs Beds/Baths
0         1.5         3  ...         False        2.0
1         1.0         2  ...          True        2.0
11        1.0         1  ...         False        1.0
14        1.0         1  ...         False        1.0
24        2.0         4  ...          True        2.0

[5 rows x 40 columns]

In [15]:
df_copy['Rooms Total'].describe

<bound method NDFrame.describe of 0        4.5
1        3.0
2        2.0
3        2.0
4        5.0
        ... 
49347    3.0
49348    2.0
49349    2.0
49350    1.0
49351    3.0
Name: Rooms Total, Length: 48817, dtype: float64>

In [16]:
df_test.shape

(16973, 40)

In [32]:
import pandas as pd

#Step 1 - importing the appropriate estimator, in this case, Linear Regression
from sklearn.linear_model import LinearRegression

#choosing model hyperparamaters by instantiating class with "model" in this case
model = LinearRegression()

#Arranging into features matrix and target matrix. 
features = ['Rooms Total']
target = ['price']
x=df_train[features]
y=df_train[target]

#check
#print(x.shape, y.shape)

#fit the model to the data..
model.fit(x,y)

#Apply the model to some new data...
total_rooms = 3
x_test = [[total_rooms]]
y_pred = model.predict(x_test)

print(f'Predicted monthly price for an apartment with {total_rooms} total rooms in New York City is: ${y_pred[0]}.')


Predicted monthly price for an apartment with 3 total rooms in New York City is: $[3792.53016946].


In [18]:
import plotly.express as px
px.scatter(df_copy, x='Rooms Total', y='price', trendline='ols')

In [19]:
from sklearn.metrics import mean_absolute_error
y_test = [3500]
mae = mean_absolute_error(y_test, y_pred)
print(f'This models error: {mae}')

This models error: 292.5301694622908


In [20]:
#intercept and coefficient
model.intercept_, model.coef_

(array([1363.48602141]), array([[809.68138268]]))

In [21]:
preds = model.predict(x)
mae = mean_absolute_error(y, preds)
print(f'Our models MAE from all the data is: ${round(mae,2)}')

Our models MAE from all the data is: $893.96


In [22]:
from sklearn.metrics import mean_squared_error
rmse = mean_squared_error(y, preds)
print(f'Our models RMSE from all the data is: ${round(rmse,2)}')

Our models RMSE from all the data is: $1798028.67


In [23]:
from sklearn.metrics import r2_score
r2 = r2_score(y, preds)
print(f'Our models R^2 from all the data is: {round(r2,2)}')

Our models R^2 from all the data is: 0.42


In [0]:
#lets try it again with another feature and see if we get a better error.

In [25]:
import pandas as pd

#Step 1 - importing the appropriate estimator, in this case, Linear Regression
from sklearn.linear_model import LinearRegression

#choosing model hyperparamaters by instantiating class with "model" in this case
model = LinearRegression()

#Arranging into features matrix and target matrix. 
features = ['# of Perks']
target = ['price']
x=df_train[features]
y=df_train[target]

#check
#print(x.shape, y.shape)

#fit the model to the data..
model.fit(x,y)

#Apply the model to some new data...
perks = 15
x_test = [[perks]]
y_pred = model.predict(x_test)

print(f'Predicted monthly price for an apartment with {perks} total rooms in New York City is: ${y_pred[0]}.')


Predicted monthly price for an apartment with 15 total rooms in New York City is: $[5168.32539986].


In [26]:
import plotly.express as px
px.scatter(df_copy, x='# of Perks', y='price', trendline='ols')

In [27]:
preds = model.predict(x)
mae = mean_absolute_error(y, preds)
print(f'Our models MAE from all the data is: ${round(mae,2)}')

Our models MAE from all the data is: $1139.72


In [28]:
from sklearn.metrics import mean_squared_error
rmse = mean_squared_error(y, preds)
print(f'Our models RMSE from all the data is: ${round(rmse,2)}')

Our models RMSE from all the data is: $2821362.01


In [29]:
from sklearn.metrics import r2_score
r2 = r2_score(y, preds)
print(f'Our models R^2 from all the data is: {round(r2,2)}')

Our models R^2 from all the data is: 0.09


In [0]:
df['Description Length'] = df['Description Length'].fillna(0)

In [31]:
import plotly.express as px
px.scatter(df_copy, x='Description Length', y='price', trendline='ols')